In [1]:
from tensorflow.keras import callbacks, optimizers
from Data.yolov4_210.py_src.yolov4.tf import SaveWeightsCallback, YOLOv4
import time
import datetime

start = datetime.datetime.now()
print( start )

yolo = YOLOv4(tiny=True)
yolo.classes = "/nfs/Shared/Data/Wildtrack.names"
yolo.input_size = 608
yolo.batch_size = 32

yolo.make_model(activation1="relu")
yolo.load_weights(
    "/nfs/Shared/Data/yolov4-tiny.conv.29_AlexeyAB",
    weights_type="yolo"
)

train_data_set = yolo.load_dataset(
    "/nfs/Shared/Data/coco_train_only_person.txt",
    image_path_prefix="/nfs/Shared/Data/train2017",
    label_smoothing=0.05
)
val_data_set = yolo.load_dataset(
    "/nfs/Shared/Data/coco_val_only_person.txt",
    image_path_prefix="/nfs/Shared/Data/val2017",
    training=False
)

epochs = 400
lr = 1e-4

optimizer = optimizers.Adam(learning_rate=lr)
yolo.compile(optimizer=optimizer, loss_iou_type="ciou")

def lr_scheduler(epoch):
    if epoch < int(epochs * 0.5):
        return lr
    if epoch < int(epochs * 0.8):
        return lr * 0.5
    if epoch < int(epochs * 0.9):
        return lr * 0.1
    return lr * 0.01

_callbacks = [
    callbacks.LearningRateScheduler(lr_scheduler),
    callbacks.TerminateOnNaN(),
    callbacks.TensorBoard(
        log_dir="/nfs/Workspace/yolov4_210_coco_only_person/logs",
    ),
    SaveWeightsCallback(
        yolo=yolo, dir_path="/nfs/Workspace/yolov4_210_coco_only_person/trained",
        weights_type="yolo", epoch_per_save=10
    ),
]

yolo.fit(
    train_data_set,
    epochs=epochs,
    callbacks=_callbacks,
    validation_data=val_data_set,
    validation_steps=50,
    validation_freq=5,
    steps_per_epoch=100,
)

end = datetime.datetime.now()
print("start:" ,start)
print("end:" ,end)
print("total:" ,end - start)

Call tf.config.experimental.set_memory_growth(GPU0, True)
2021-03-07 08:56:58.230083
Epoch 1/400
grid: 38*38 iou_loss: 20.0727081 conf_loss: 2939.17529 prob_loss: 4.03612614 total_loss 2963.28418
grid: 19*19 iou_loss: 14.5469913 conf_loss: 792.272095 prob_loss: 3.16364288 total_loss 809.982727
grid: 38*38 iou_loss: 20.0135803 conf_loss: 2905.96973 prob_loss: 3.83355522 total_loss 2929.81689
grid: 19*19 iou_loss: 11.7802372 conf_loss: 776.546753 prob_loss: 2.53332043 total_loss 790.860291
grid: 38*38 iou_loss: 11.472744 conf_loss: 2873.19336 prob_loss: 2.32182288 total_loss 2886.98779
grid: 19*19 iou_loss: 12.782939 conf_loss: 761.29895 prob_loss: 2.95057058 total_loss 777.032471
grid: 38*38 iou_loss: 16.6402302 conf_loss: 2840.90845 prob_loss: 3.3768487 total_loss 2860.92554
grid: 19*19 iou_loss: 11.9848499 conf_loss: 746.927368 prob_loss: 2.61303854 total_loss 761.525269
grid: 38*38 iou_loss: 13.4629517 conf_loss: 2812.25146 prob_loss: 2.64643 total_loss 2828.36084
grid: 19*19 iou_los

In [2]:
from Data.yolov4_210.py_src.yolov4.tf import YOLOv4

yolo = YOLOv4(tiny=True, tpu=True)

yolo.classes = "/nfs/Shared/Data/Wildtrack.names"
yolo.input_size = (512, 384) # width, height
yolo.make_model(activation1="relu")

yolo.load_weights("/nfs/Workspace/yolov4_210_coco_only_person/trained/yolov4-tiny-170.weights", weights_type="yolo")

dataset = yolo.load_dataset(
    "/nfs/Shared/Data/coco_train_only_person.txt",
    training=False,
    image_path_prefix="/nfs/Shared/Data/train2017"
)

yolo.save_as_tflite(
    "/nfs/Workspace/yolov4_210_coco_only_person/convert_model/yolov4-tiny-170-relu-int8.tflite",
    quantization="full_int8",
    data_set=dataset,
    num_calibration_steps=400
)

INFO:tensorflow:Assets written to: /tmp/tmp3duz0j10/assets


In [3]:
!edgetpu_compiler -sa /nfs/Workspace/yolov4_210_coco_only_person/convert_model/yolov4-tiny-170-relu-int8.tflite -o /nfs/Workspace/yolov4_210_coco_only_person/convert_model

Edge TPU Compiler version 15.0.340273435

Model compiled successfully in 1383 ms.

Input model: /nfs/Workspace/yolov4_210_coco_only_person/convert_model/yolov4-tiny-170-relu-int8.tflite
Input size: 5.75MiB
Output model: /nfs/Workspace/yolov4_210_coco_only_person/convert_model/yolov4-tiny-170-relu-int8_edgetpu.tflite
Output size: 5.92MiB
On-chip memory used for caching model parameters: 5.69MiB
On-chip memory remaining for caching model parameters: 1.80MiB
Off-chip memory used for streaming uncached model parameters: 3.38KiB
Number of Edge TPU subgraphs: 3
Total number of operations: 132
Operation log: /nfs/Workspace/yolov4_210_coco_only_person/convert_model/yolov4-tiny-170-relu-int8_edgetpu.log

Model successfully compiled but not all operations are supported by the Edge TPU. A percentage of the model will instead run on the CPU, which is slower. If possible, consider updating your model to use only operations supported by the Edge TPU. For details, visit g.co/coral/model-reqs.
Number 

In [4]:
from Data.yolov4_210.py_src.yolov4.tf import YOLOv4

yolo = YOLOv4(tiny=True, tpu=True)

yolo.classes = "/nfs/Shared/Data/Wildtrack.names"
yolo.input_size = (512, 384) # width, height
yolo.make_model(activation1="relu")

yolo.load_weights("/nfs/Workspace/yolov4_210_coco_only_person/trained/yolov4-tiny-160.weights", weights_type="yolo")

dataset = yolo.load_dataset(
    "/nfs/Shared/Data/coco_train_only_person.txt",
    training=False,
    image_path_prefix="/nfs/Shared/Data/train2017"
)

yolo.save_as_tflite(
    "/nfs/Workspace/yolov4_210_coco_only_person/convert_model/yolov4-tiny-160-relu-int8.tflite",
    quantization="full_int8",
    data_set=dataset,
    num_calibration_steps=400
)

INFO:tensorflow:Assets written to: /tmp/tmp8vvg6wz7/assets


INFO:tensorflow:Assets written to: /tmp/tmp8vvg6wz7/assets


In [2]:
import os
os.chdir("../..")
print(os.getcwd())
from yolov4_210.yolov4_210.py_src.yolov4.tflite import YOLOv4
os.chdir("/home/css-wu/Documents/Machine_Learning/YoloV4/hhk7734/NTUT_AI_Platform/yolov4_210_coco_only_person")
import cv2

yolo = YOLOv4(tiny=True, tpu=True)

yolo.classes = "/home/css-wu/Documents/Machine_Learning/YoloV4/hhk7734/Wildtrack.names"

yolo.load_tflite("convert_model/yolov4-tiny-170-relu-int8_edgetpu.tflite")

yolo.inference(
    "/home/css-wu/CloudStation/Data/cam6.mp4",
    is_image=False,
    cv_apiPreference=cv2.CAP_ANY,
    # cv_waitKey_delay= 25,
    cv_frame_size=(1920, 1080),
    cv_fourcc="YUYV",
)

/home/css-wu/Documents/Machine_Learning/YoloV4/hhk7734
YOLOv4: Inference is finished
